In [1]:
import pandas as pd

# Read in Data

In [203]:
traindemographics=pd.read_csv(r"C:\Users\Mahar\Desktop\Interview\train\traindemographics.csv")
trainperf=pd.read_csv(r"C:\Users\Mahar\Desktop\Interview\train\trainperf.csv")
trainprevloans=pd.read_csv(r"C:\Users\Mahar\Desktop\Interview\train\trainprevloans.csv")

# Data Quality tests

In [3]:
import pandas_profiling 

In [4]:
# This step takes very long, please be patient

profile_traindemographics = pandas_profiling.ProfileReport(traindemographics)
profile_trainperf=pandas_profiling.ProfileReport(trainperf)
profile_trainprevloans=pandas_profiling.ProfileReport(trainprevloans)

##traindemographics
print('Running EDA for traindemographics')
try:
    traindemographics_rejected_variables = profile_traindemographics.get_rejected_variables(threshold =0.9)
except: 
    print('No numeric vars')
    
## trainperf   
print('Running EDA for trainperf')  
try:
    trainperf_rejected_variables = profile_trainperf.get_rejected_variables(threshold =0.9)
except: 
    print('No numeric vars')
    
##   trainprevloans
print('Running EDA for trainprevloans')  
try:
    trainprevloans_rejected_variables = profile_trainprevloans.get_rejected_variables(threshold =0.9)
except: print('No numeric vars')   
    

C:\Users\Mahar\AppData\Roaming\Python\Python36\site-packages\pandas_profiling\model\correlations.py:124: UserWarning: There was an attempt to calculate the cramers correlation, but this failed.
To hide this warning, disable the calculation
(using `df.profile_report(correlations={"cramers": False}`)
If this is problematic for your use case, please report this as an issue:
https://github.com/pandas-profiling/pandas-profiling/issues
(include the error message: 'The internally computed table of expected frequencies has a zero element at (0, 11).')
  correlation_name=correlation_name, error=error


Running EDA for traindemographics
Running EDA for trainperf
Running EDA for trainprevloans


# Traindemographics results

In [5]:
profile_traindemographics

# trainperf Results

In [6]:
profile_trainperf

# trainprevloans Results

In [8]:
profile_trainprevloans

# Find constant Columns

In [9]:
traindemographics_constant_columns =list(traindemographics.loc[:,traindemographics.apply(lambda x:x.nunique())==1])
trainperf_constant_columns =list(trainperf.loc[:,trainperf.apply(lambda x:x.nunique())==1])
trainprevloans_constant_columns =list(trainprevloans.loc[:,trainprevloans.apply(lambda x:x.nunique())==1])

# Null Handeling 

In [ ]:
#Function for handeling nulls
def null_handling(data,value,null_mean_replace_columns=[],null_mode_replace_columns=[],null_custom_replace_columns=[],column_to_look_through=[]):
    # Replace nulls with the mean of the column 
    #null_mean_replace_columns=[]
    if len(null_mean_replace_columns)>0:
        data[null_mean_replace_columns]=data[null_mean_replace_columns].fillna(data[null_mean_replace_columns].mean())

    # Replace nulls with the mode of the column 
    #null_mode_replace_columns=[]
    if len(null_mode_replace_columns)>0:
        data[null_mode_replace_columns]=data[null_mode_replace_columns].fillna(data[null_mode_replace_columns].mode())

    # Replace nulls with custom value
    #value =
    null_custom_replace_columns=[]
    if len(null_custom_replace_columns)>0:
        data[null_custom_replace_columns]=data[null_custom_replace_columns].fillna(value)


    # Drop rows with nulls
    #column_to_look_through = []
    if len(column_to_look_through)>0:
        dat=data.dropna(subset=column_to_look_through)
    return(data)

In [204]:
#create an early payemnt indicator

trainprevloans['dayspaidbeforedue']=(pd.to_datetime(trainprevloans['firstduedate'])- pd.to_datetime(trainprevloans['firstrepaiddate'])).dt.days
trainprevloans['earlypayment']=0
trainprevloans['earlypayment'][trainprevloans['dayspaidbeforedue']>=0]=1


In [205]:
trainprevloans['was_referred']=1
trainprevloans['was_referred'][trainprevloans['referredby'].isna()]=0

# Feature creation and dataset manipulation

In [206]:
#number of loans per client in each term
#need to join this back up and filna to 0 after all
f15_day_data=trainprevloans[trainprevloans['termdays']==15].groupby('customerid').aggregate({'termdays': 'count'})
f30_day_data=trainprevloans[trainprevloans['termdays']==30].groupby('customerid').aggregate({'termdays': 'count'})
f60_day_data=trainprevloans[trainprevloans['termdays']==60].groupby('customerid').aggregate({'termdays': 'count'})
f90_day_data=trainprevloans[trainprevloans['termdays']==90].groupby('customerid').aggregate({'termdays': 'count'})

In [207]:
#number of loans per client in each term that were late
#need to join this back up
late_f15_day_data=trainprevloans[(trainprevloans['termdays']==15)  & ( trainprevloans['earlypayment']==0)].groupby('customerid').aggregate({'termdays': 'count'})
late_f30_day_data=trainprevloans[(trainprevloans['termdays']==30)  & ( trainprevloans['earlypayment']==0)].groupby('customerid').aggregate({'termdays': 'count'})
late_f60_day_data=trainprevloans[(trainprevloans['termdays']==60 ) &  (trainprevloans['earlypayment']==0)].groupby('customerid').aggregate({'termdays': 'count'})
late_f90_day_data=trainprevloans[(trainprevloans['termdays']==90 ) &  (trainprevloans['earlypayment']==0)].groupby('customerid').aggregate({'termdays': 'count'})

In [208]:
#ever referred
referred=trainprevloans.groupby('customerid').aggregate({'was_referred': 'max'})

In [209]:
#ever been late on a payment
late_pay=trainprevloans.groupby('customerid').aggregate({'earlypayment': 'min'})

# ever been early on a payment
early_pay=trainprevloans.groupby('customerid').aggregate({'earlypayment': 'max'})

In [210]:
main=trainprevloans.groupby('customerid').aggregate({'was_referred': 'count'})

In [211]:
main=main.join(referred,how='left',rsuffix='_ever_referred_')
main=main.join(late_pay,how='left',rsuffix='_late_paid_')
main=main.join(early_pay,how='left',rsuffix='_early_paid_')


main=main.join(f15_day_data,how='left',rsuffix='_f15_day_data_')
main=main.join(f30_day_data,how='left',rsuffix='_f30_day_data_')
main=main.join(f60_day_data,how='left',rsuffix='_f60_day_data_')
main=main.join(f90_day_data,how='left',rsuffix='_f90_day_data_')


main=main.join(late_f15_day_data,how='left',rsuffix='_late_f15_day_data_')
main=main.join(late_f30_day_data,how='left',rsuffix='_late_f30_day_data_')
main=main.join(late_f60_day_data,how='left',rsuffix='_late_f60_day_data_')
main=main.join(late_f90_day_data,how='left',rsuffix='_late_f90_day_data_')

main=main.fillna(0)

In [212]:
traindemo=traindemographics[['customerid','birthdate','bank_account_type','bank_name_clients','employment_status_clients','level_of_education_clients']]
traindemo=traindemo.fillna('not given')
traindemo=traindemo.set_index('customerid')

In [213]:
trainperf_final=trainperf[['customerid','loannumber','creationdate','loanamount','totaldue','good_bad_flag']]
trainperf_final=trainperf_final.set_index('customerid')

In [214]:
final_train=trainperf_final.join(traindemo,how='left',rsuffix='_demo')
final_train=final_train.join(main,how='left',rsuffix='_main')
final_train=final_train.fillna(0)

In [216]:
final_train.to_csv(r"C:\Users\Mahar\Desktop\Interview\train\final_set.csv")

In [215]:
list(final_train)

['loannumber',
 'creationdate',
 'loanamount',
 'totaldue',
 'good_bad_flag',
 'birthdate',
 'bank_account_type',
 'bank_name_clients',
 'employment_status_clients',
 'level_of_education_clients',
 'was_referred',
 'was_referred_ever_referred_',
 'earlypayment',
 'earlypayment_early_paid_',
 'termdays',
 'termdays_f30_day_data_',
 'termdays_f60_day_data_',
 'termdays_f90_day_data_',
 'termdays_late_f15_day_data_',
 'termdays_late_f30_day_data_',
 'termdays_late_f60_day_data_',
 'termdays_late_f90_day_data_']

# Encode vars

In [151]:
Dummy_Cat_vars=['good_bad_flag','bank_account_type','bank_name_clients','employment_status_clients','level_of_education_clients']
for i in Dummy_Cat_vars:
    final_train[i]=final_train[i].astype('category')
    final_train[i]=final_train[i].cat.codes

final_train=final_train.drop(['creationdate','birthdate'],axis=1)

In [165]:
import sklearn
from sklearn.model_selection import train_test_split
from sklearn.ensemble import GradientBoostingClassifier
from sklearn.tree import DecisionTreeClassifier
from sklearn.ensemble import RandomForestClassifier

Y=final_train['good_bad_flag'].values.ravel()
X=final_train.drop(['good_bad_flag'],axis=1).values


X_train,X_test,Y_train,Y_test=train_test_split(X,Y,test_size=0.3)

#GBM

print('Running GBM')
GBM_Classifier=GradientBoostingClassifier(n_estimators=100,learning_rate=0.1,max_depth=3,random_state=0)
GBM_Classifier.fit(X_train,Y_train)
GBM_Classifier_prediction=GBM_Classifier.predict(X_test)

print('Running Decision tree')
DT_Classifier=DecisionTreeClassifier(random_state=0)
DT_Classifier.fit(X_train,Y_train)
DT_Classifier_prediction=DT_Classifier.predict(X_test)

print('Running random forest')
RF_Classifier=RandomForestClassifier(n_estimators=10,random_state=0,n_jobs=-1)
RF_Classifier.fit(X_train,Y_train)
RF_Classifier_prediction=RF_Classifier.predict(X_test)


Running GBM
Running Decision tree
Running random forest


# Test set accuracy scores

In [166]:
RF_Classifier.score(X_test,Y_test)


0.741051028179741

In [167]:
DT_Classifier.score(X_test,Y_test)

0.6945925361766946

In [168]:
GBM_Classifier.score(X_test,Y_test)

0.7814166031987814

# Going to use GBM

In [183]:
traindemographics=pd.read_csv(r"C:\Users\Mahar\Desktop\Interview\test\testdemographics.csv")
trainperf=pd.read_csv(r"C:\Users\Mahar\Desktop\Interview\test\testperf.csv")
trainprevloans=pd.read_csv(r"C:\Users\Mahar\Desktop\Interview\test\testprevloans.csv")

In [186]:
#create an early payemnt indicator

trainprevloans['dayspaidbeforedue']=(pd.to_datetime(trainprevloans['firstduedate'])- pd.to_datetime(trainprevloans['firstrepaiddate'])).dt.days
trainprevloans['earlypayment']=0
trainprevloans['earlypayment'][trainprevloans['dayspaidbeforedue']>=0]=1


trainprevloans['was_referred']=1
trainprevloans['was_referred'][trainprevloans['referredby'].isna()]=0

#number of loans per client in each term
#need to join this back up and filna to 0 after all
f15_day_data=trainprevloans[trainprevloans['termdays']==15].groupby('customerid').aggregate({'termdays': 'count'})
f30_day_data=trainprevloans[trainprevloans['termdays']==30].groupby('customerid').aggregate({'termdays': 'count'})
f60_day_data=trainprevloans[trainprevloans['termdays']==60].groupby('customerid').aggregate({'termdays': 'count'})
f90_day_data=trainprevloans[trainprevloans['termdays']==90].groupby('customerid').aggregate({'termdays': 'count'})


#number of loans per client in each term that were late
#need to join this back up
late_f15_day_data=trainprevloans[(trainprevloans['termdays']==15)  & ( trainprevloans['earlypayment']==0)].groupby('customerid').aggregate({'termdays': 'count'})
late_f30_day_data=trainprevloans[(trainprevloans['termdays']==30)  & ( trainprevloans['earlypayment']==0)].groupby('customerid').aggregate({'termdays': 'count'})
late_f60_day_data=trainprevloans[(trainprevloans['termdays']==60 ) &  (trainprevloans['earlypayment']==0)].groupby('customerid').aggregate({'termdays': 'count'})
late_f90_day_data=trainprevloans[(trainprevloans['termdays']==90 ) &  (trainprevloans['earlypayment']==0)].groupby('customerid').aggregate({'termdays': 'count'})


#ever referred
referred=trainprevloans.groupby('customerid').aggregate({'was_referred': 'max'})


#ever been late on a payment
late_pay=trainprevloans.groupby('customerid').aggregate({'earlypayment': 'min'})

# ever been early on a payment
early_pay=trainprevloans.groupby('customerid').aggregate({'earlypayment': 'max'})


main=trainprevloans.groupby('customerid').aggregate({'was_referred': 'count'})



main=main.join(referred,how='left',rsuffix='_ever_referred_')
main=main.join(late_pay,how='left',rsuffix='_late_paid_')
main=main.join(early_pay,how='left',rsuffix='_early_paid_')


main=main.join(f15_day_data,how='left',rsuffix='_f15_day_data_')
main=main.join(f30_day_data,how='left',rsuffix='_f30_day_data_')
main=main.join(f60_day_data,how='left',rsuffix='_f60_day_data_')
main=main.join(f90_day_data,how='left',rsuffix='_f90_day_data_')


main=main.join(late_f15_day_data,how='left',rsuffix='_late_f15_day_data_')
main=main.join(late_f30_day_data,how='left',rsuffix='_late_f30_day_data_')
main=main.join(late_f60_day_data,how='left',rsuffix='_late_f60_day_data_')
main=main.join(late_f90_day_data,how='left',rsuffix='_late_f90_day_data_')

main=main.fillna(0)



traindemo=traindemographics[['customerid','birthdate','bank_account_type','bank_name_clients','employment_status_clients','level_of_education_clients']]
traindemo=traindemo.fillna('not given')
traindemo=traindemo.set_index('customerid')


trainperf_final=trainperf[['customerid','loannumber','creationdate','loanamount','totaldue']]
trainperf_final=trainperf_final.set_index('customerid')



final_test=trainperf_final.join(traindemo,how='left',rsuffix='_demo')
final_test=final_test.join(main,how='left',rsuffix='_main')
final_test=final_test.fillna(0)


Dummy_Cat_vars=['bank_account_type','bank_name_clients','employment_status_clients','level_of_education_clients']
for i in Dummy_Cat_vars:
    final_test[i]=final_test[i].astype('category')
    final_test[i]=final_test[i].cat.codes

final_test=final_test.drop(['creationdate','birthdate'],axis=1)

Y_train=final_train['good_bad_flag'].values.ravel()
X_train=final_train.drop(['good_bad_flag'],axis=1).values


X_test=final_test.values


In [187]:
import sklearn
from sklearn.model_selection import train_test_split
from sklearn.ensemble import GradientBoostingClassifier
from sklearn.tree import DecisionTreeClassifier
from sklearn.ensemble import RandomForestClassifier



#GBM

print('Running GBM')
GBM_Classifier=GradientBoostingClassifier(n_estimators=100,learning_rate=0.1,max_depth=3,random_state=0)
GBM_Classifier.fit(X_train,Y_train)
GBM_Classifier_prediction=GBM_Classifier.predict(X_test)

print('Running Decision tree')
DT_Classifier=DecisionTreeClassifier(random_state=0)
DT_Classifier.fit(X_train,Y_train)
DT_Classifier_prediction=DT_Classifier.predict(X_test)

print('Running random forest')
RF_Classifier=RandomForestClassifier(n_estimators=10,random_state=0,n_jobs=-1)
RF_Classifier.fit(X_train,Y_train)
RF_Classifier_prediction=RF_Classifier.predict(X_test)

Running GBM
Running Decision tree
Running random forest


In [201]:
pd.merge([final_test,pd.DataFrame(GBM_Classifier_prediction)],axis=0)

loannumber  loanamount  totaldue  \
8a28afc7474813a40147639ec637156b        11.0     25000.0   27500.0   
8a3735d5518aba7301518ac34413010d         7.0     20000.0   24500.0   
8a76e7d443e6e97c0143ed099d102b1d         6.0     20000.0   24500.0   
8a818823525dceef01525deda2480384        10.0     40000.0   48000.0   
8a818926522ea5ef01523aff15c37482         3.0     20000.0   24500.0   
8a8189f9526ad7de015280bef19d5811        13.0     10000.0   10500.0   
8a85880353acff880153b92f8599568b         7.0     30000.0   34500.0   
8a85880353acff880153b9993fe358d9         9.0     30000.0   34500.0   
8a85880353acff880153bd56e93f75ff         4.0     20000.0   24500.0   
8a85881053bc33670153bda8562417c7         2.0     10000.0   13000.0   
8a85881053bc33670153c79e8e84571a         2.0     10000.0   13000.0   
8a85881053bc33670153c7a0e6ee582e        12.0     40000.0   44000.0   
8a8588175489ef7701548cd088f2207b         3.0     10000.0   13000.0   
8a85881a5420ebf101543716beee1039         7.0     30000.0   39000.0   
8a8588235375c27f01537fd31b1f53cd         6.0     30000.0   34500.0   
8a8588235384a58d01539f23b1071fd9        14.0     40000.0   48000.0   
8a8588235384a58d0153a1e7fa6a5089        12.0     40000.0   44000.0   
8a8588235384a58d0153a80649f43890         9.0     30000.0   34500.0   
8a85882653d0bb500153d96597b72471         4.0     10000.0   13000.0   
8a85882953bc04f80153bc05a36c0003        14.0     40000.0   44000.0   
8a85883353d0c4e90153d24b9d0667bd        12.0     50000.0   52500.0   
8a85883353d0c4e90153d308b87e7f1a        13.0     40000.0   44000.0   
8a85883353e2e4e40153e615982440e2         8.0     10000.0   13000.0   
8a85883353e2e4e40153eca57a9855c6        13.0     25000.0   27500.0   
8a85884e548fad6501549e6d40590168        13.0     30000.0   34500.0   
8a85884e54a0565b0154a05a7dd10159         6.0     10000.0   11500.0   
8a85884e54be33290154c3f438574c05         7.0     25000.0   28750.0   
8a85886e54beabf90154cabe9155402d         8.0     30000.0   39000.0   
8a85886f543912e301543dfa84bb3132        11.0     15000.0   16687.5   
8a85886f543912e301543e0badb035fa         5.0     10000.0   13000.0   
...                                      ...         ...       ...   
1420                                     NaN         NaN       NaN   
1421                                     NaN         NaN       NaN   
1422                                     NaN         NaN       NaN   
1423                                     NaN         NaN       NaN   
1424                                     NaN         NaN       NaN   
1425                                     NaN         NaN       NaN   
1426                                     NaN         NaN       NaN   
1427                                     NaN         NaN       NaN   
1428                                     NaN         NaN       NaN   
1429                                     NaN         NaN       NaN   
1430                                     NaN         NaN       NaN   
1431                                     NaN         NaN       NaN   
1432                                     NaN         NaN       NaN   
1433                                     NaN         NaN       NaN   
1434                                     NaN         NaN       NaN   
1435                                     NaN         NaN       NaN   
1436                                     NaN         NaN       NaN   
1437                                     NaN         NaN       NaN   
1438                                     NaN         NaN       NaN   
1439                                     NaN         NaN       NaN   
1440                                     NaN         NaN       NaN   
1441                                     NaN         NaN       NaN   
1442                                     NaN         NaN       NaN   
1443                                     NaN         NaN       NaN   
1444                                     NaN         NaN       NaN   
1445                                     NaN

In [202]:
pd.DataFrame(GBM_Classifier_prediction).to_csv(r"C:\Users\Mahar\Desktop\Interview\answer.csv")